<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#rewritten-version-of-the-SQL-pipeline" data-toc-modified-id="rewritten-version-of-the-SQL-pipeline-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>rewritten version of the SQL pipeline</a></span></li></ul></div>

## rewritten version of the SQL pipeline
reading H5s from the S3 bucket in EMR+pyspark was giving me a headache, so i decided to just preprocess the h5s into easy CSVs and sync them this way. so i'll have... 39k CSV files, which can be read more easily in EMR notebook, and concatenated into one big RDD.

this takes about 2 hours to save locally, probably another half hour to upload to S3. if working with bigger data, i would ideally find a way to wrangle the .h5s directly in spark.

In [2]:
import pandas as pd
import numpy as np
import pandas as pd
import mysql.connector
from tqdm import tqdm
import h5py
from sqlalchemy import types, create_engine 
import os
from os import listdir
from os.path import isfile, join
import config
import time

In [23]:
def get_files_list(): # gets list of filepath strings in ~/data
    mypath = os.getcwd()+'/data/'
    files = [f for f in listdir(mypath) if isfile(join(mypath, f))]
    for f in files:
        f = mypath+f # append full path for h5py loading
    files = list(map(lambda f: mypath+f, files))
    return files 

def process_orbit(h5): # filename string. adds h5's observations to dataframe
    # the formatting/array shape is all uniform. thanks, NASA
    f = h5py.File(h5, 'r') # read file
    geo = f['GEOLOCATION_DATA'] # h5 Groups architecture is similar to dict
    sci = f['SCIENCE_DATA']
    # hdf.Datasets -> np.array -> flatten -> list. faster than looping through each matrix
    lat = list(geo['Latitude'].value.ravel())
    long = list(geo['Longitude'].value.ravel()) # is there a less verbose way to do this?
    sat_lat = list(geo['SpacecraftLatitude'].value.ravel())*36 # extend the 1d arrays
    sat_long = list(geo['SpacecraftLongitude'].value.ravel())*36 # don't forget to ravel like i did
    sat_alt = list(geo['SpacecraftAltitude'].value.ravel())*36
    time = list(geo['TimeUTC'].value.ravel())*36 # 36 measurements per position means one "time" value for every consecutive 36 measurements
    sza = list(geo['SolarZenithAngle'].value.ravel())
    pbl = list(sci['ColumnAmountSO2_PBL'].value.ravel())
    anom = list(sci['Flag_SAA'].value.ravel())
    volc = list(sci['Flag_SO2'].value.ravel())
    # combine lists into df
    new = pd.DataFrame(list(zip(lat, long, sat_lat, sat_long, sat_alt, time, sza, pbl, anom, volc)),
                       columns=["lat", "long", "sat_lat", "sat_long", 
                                'sat_alt', "time", "sza", "pbl", "anom", 'volc'])
    new['time'] = new['time'].astype(str) # change time format
    new['time'] = new['time'].apply(lambda st: st[2:12]+' '+st[13:21]) # change time format
    return new # returns new df

def make_engine():
    user = config.user # substitute your own username, password & SQL server host
    pw = config.pw
    host = config.host
    db = config.db
    connst = f'mysql+pymysql://{user}:{pw}@{host}/{db}'
    engine = create_engine(connst, echo=False) # don't set pool_recycle
    return engine

# rewrote this method to save to local CSVs instead of pushing to SQL
# since we're just gonna "aws s3 sync" our CSVs to the S3 bucket for spark processing
def process_h5s(files, engine): # filepath strings
    # to keep track of progress
    files = get_files_list() # get filepath strings
#     engine = 
    for c,f in enumerate(tqdm(files)): # this took 18 hours for 40,000 11k-length h5 files on my laptop
        try:
            df = process_orbit(f)
        except Exception as e: print(e)
#         try:
        df.to_csv(str(c)+'.csv')
#         except Exception as e: print(e)
#         df.to_sql('so2', con=engine, if_exists='append') # sqlalchemy takes care of sessions, commits etc rather nicely
    return 

def setup(): # get engine and filestring list
    print('establishing engine...')
    engine = make_engine() # establish connection to server
    files = get_files_list() # get filepath strings
    return engine, files

In [24]:

# get engine & list of filepathstrings in /data
engine, files = setup()
print(f'processing {len(files)} files...')
# modified process method, save to /csv_data
process_h5s(files, engine) # process each file & upload to server

establishing engine...
processing 39629 files...







  0%|          | 0/39629 [00:00<?, ?it/s]




  0%|          | 1/39629 [00:00<2:10:28,  5.06it/s]




  0%|          | 2/39629 [00:00<2:08:58,  5.12it/s]




  0%|          | 3/39629 [00:00<2:09:45,  5.09it/s]




  0%|          | 4/39629 [00:00<2:10:01,  5.08it/s]




  0%|          | 5/39629 [00:00<2:08:52,  5.12it/s]




  0%|          | 6/39629 [00:01<2:07:50,  5.17it/s]




  0%|          | 7/39629 [00:01<2:08:46,  5.13it/s]




  0%|          | 8/39629 [00:01<2:10:09,  5.07it/s]




  0%|          | 9/39629 [00:01<2:11:33,  5.02it/s]




  0%|          | 10/39629 [00:01<2:13:31,  4.94it/s]




  0%|          | 11/39629 [00:02<2:14:32,  4.91it/s]




  0%|          | 12/39629 [00:02<2:15:38,  4.87it/s]




  0%|          | 13/39629 [00:02<2:16:41,  4.83it/s]




  0%|          | 14/39629 [00:02<2:19:43,  4.73it/s]




  0%|          | 15/39629 [00:03<2:19:26,  4.73it/s]




  0%|          | 16/39629 [00:03<2:18:59,  4.75it/s]




  0%|          | 17/39629 [00:03<2:19:00,  4.7

  0%|          | 113/39629 [00:24<2:23:23,  4.59it/s]




  0%|          | 114/39629 [00:24<2:23:35,  4.59it/s]




  0%|          | 115/39629 [00:24<2:25:19,  4.53it/s]




  0%|          | 116/39629 [00:24<2:32:41,  4.31it/s]




  0%|          | 117/39629 [00:25<2:33:14,  4.30it/s]




  0%|          | 118/39629 [00:25<2:34:58,  4.25it/s]




  0%|          | 119/39629 [00:25<2:34:53,  4.25it/s]




  0%|          | 120/39629 [00:25<2:31:07,  4.36it/s]




  0%|          | 121/39629 [00:26<2:27:58,  4.45it/s]




  0%|          | 122/39629 [00:26<2:25:59,  4.51it/s]




  0%|          | 123/39629 [00:26<2:24:10,  4.57it/s]




  0%|          | 124/39629 [00:26<2:23:23,  4.59it/s]




  0%|          | 125/39629 [00:26<2:23:09,  4.60it/s]




  0%|          | 126/39629 [00:27<2:23:05,  4.60it/s]




  0%|          | 127/39629 [00:27<2:22:47,  4.61it/s]




  0%|          | 128/39629 [00:27<2:22:29,  4.62it/s]




  0%|          | 129/39629 [00:27<2:23:14,  4.60it/s]




  0%|         

  1%|          | 226/39629 [00:49<2:24:47,  4.54it/s]




  1%|          | 227/39629 [00:49<2:28:14,  4.43it/s]




  1%|          | 228/39629 [00:49<2:33:57,  4.27it/s]




  1%|          | 229/39629 [00:49<2:33:15,  4.28it/s]




  1%|          | 230/39629 [00:50<2:30:33,  4.36it/s]




  1%|          | 231/39629 [00:50<2:31:03,  4.35it/s]




  1%|          | 232/39629 [00:50<2:33:51,  4.27it/s]




  1%|          | 233/39629 [00:50<2:30:21,  4.37it/s]




  1%|          | 234/39629 [00:51<2:27:33,  4.45it/s]




  1%|          | 235/39629 [00:51<2:26:42,  4.48it/s]




  1%|          | 236/39629 [00:51<2:29:30,  4.39it/s]




  1%|          | 237/39629 [00:51<2:30:38,  4.36it/s]




  1%|          | 238/39629 [00:51<2:29:38,  4.39it/s]




  1%|          | 239/39629 [00:52<2:31:20,  4.34it/s]




  1%|          | 240/39629 [00:52<2:28:25,  4.42it/s]




  1%|          | 241/39629 [00:52<3:08:06,  3.49it/s]




  1%|          | 242/39629 [00:53<2:54:08,  3.77it/s]




  1%|         

  1%|          | 338/39629 [01:14<2:20:02,  4.68it/s]




  1%|          | 339/39629 [01:14<2:20:13,  4.67it/s]




  1%|          | 340/39629 [01:14<2:20:26,  4.66it/s]




  1%|          | 341/39629 [01:14<2:19:19,  4.70it/s]




  1%|          | 342/39629 [01:15<2:19:59,  4.68it/s]




  1%|          | 343/39629 [01:15<2:20:42,  4.65it/s]




  1%|          | 344/39629 [01:15<2:19:24,  4.70it/s]




  1%|          | 345/39629 [01:15<2:19:23,  4.70it/s]




  1%|          | 346/39629 [01:15<2:19:31,  4.69it/s]




  1%|          | 347/39629 [01:16<2:18:58,  4.71it/s]




  1%|          | 348/39629 [01:16<2:19:40,  4.69it/s]




  1%|          | 349/39629 [01:16<2:19:49,  4.68it/s]




  1%|          | 350/39629 [01:16<2:19:45,  4.68it/s]




  1%|          | 351/39629 [01:16<2:17:38,  4.76it/s]




  1%|          | 352/39629 [01:17<2:18:33,  4.72it/s]




  1%|          | 353/39629 [01:17<2:18:55,  4.71it/s]




  1%|          | 354/39629 [01:17<2:19:08,  4.70it/s]




  1%|         

...

 99%|█████████▉| 39221/39629 [2:41:05<01:52,  3.63it/s]




 99%|█████████▉| 39222/39629 [2:41:05<01:53,  3.60it/s]




 99%|█████████▉| 39223/39629 [2:41:05<01:51,  3.63it/s]




 99%|█████████▉| 39224/39629 [2:41:05<01:51,  3.64it/s]




 99%|█████████▉| 39225/39629 [2:41:06<01:52,  3.60it/s]




 99%|█████████▉| 39226/39629 [2:41:06<01:52,  3.60it/s]




 99%|█████████▉| 39227/39629 [2:41:06<01:51,  3.62it/s]




 99%|█████████▉| 39228/39629 [2:41:06<01:51,  3.61it/s]




 99%|█████████▉| 39229/39629 [2:41:07<01:52,  3.57it/s]




 99%|█████████▉| 39230/39629 [2:41:07<01:51,  3.59it/s]




 99%|█████████▉| 39231/39629 [2:41:07<01:50,  3.61it/s]




 99%|█████████▉| 39232/39629 [2:41:08<01:49,  3.61it/s]




 99%|█████████▉| 39233/39629 [2:41:08<01:50,  3.59it/s]




 99%|█████████▉| 39234/39629 [2:41:08<01:49,  3.61it/s]




 99%|█████████▉| 39235/39629 [2:41:08<01:48,  3.63it/s]




 99%|█████████▉| 39236/39629 [2:41:09<01:51,  3.54it/s]




 99%|█████████▉| 39237/39629 [2:41:09<01

 99%|█████████▉| 39330/39629 [2:41:35<01:22,  3.61it/s]




 99%|█████████▉| 39331/39629 [2:41:35<01:22,  3.61it/s]




 99%|█████████▉| 39332/39629 [2:41:35<01:22,  3.62it/s]




 99%|█████████▉| 39333/39629 [2:41:36<01:21,  3.61it/s]




 99%|█████████▉| 39334/39629 [2:41:36<01:21,  3.63it/s]




 99%|█████████▉| 39335/39629 [2:41:36<01:21,  3.62it/s]




 99%|█████████▉| 39336/39629 [2:41:36<01:20,  3.62it/s]




 99%|█████████▉| 39337/39629 [2:41:37<01:22,  3.53it/s]




 99%|█████████▉| 39338/39629 [2:41:37<01:21,  3.56it/s]




 99%|█████████▉| 39339/39629 [2:41:37<01:22,  3.53it/s]




 99%|█████████▉| 39340/39629 [2:41:38<01:21,  3.55it/s]




 99%|█████████▉| 39341/39629 [2:41:38<01:22,  3.49it/s]




 99%|█████████▉| 39342/39629 [2:41:38<01:21,  3.51it/s]




 99%|█████████▉| 39343/39629 [2:41:38<01:22,  3.46it/s]




 99%|█████████▉| 39344/39629 [2:41:39<01:22,  3.46it/s]




 99%|█████████▉| 39345/39629 [2:41:39<01:21,  3.51it/s]




 99%|█████████▉| 39346/39629 [2:41:39<01

Unable to open file (file signature not found)







 99%|█████████▉| 39422/39629 [2:42:01<00:55,  3.71it/s]




 99%|█████████▉| 39423/39629 [2:42:01<00:56,  3.65it/s]




 99%|█████████▉| 39424/39629 [2:42:01<00:52,  3.90it/s]




 99%|█████████▉| 39425/39629 [2:42:02<00:53,  3.79it/s]




 99%|█████████▉| 39426/39629 [2:42:02<00:55,  3.64it/s]




 99%|█████████▉| 39427/39629 [2:42:02<00:55,  3.67it/s]




 99%|█████████▉| 39428/39629 [2:42:02<00:55,  3.63it/s]




 99%|█████████▉| 39429/39629 [2:42:03<00:54,  3.65it/s]




 99%|█████████▉| 39430/39629 [2:42:03<00:54,  3.62it/s]




100%|█████████▉| 39431/39629 [2:42:03<00:54,  3.65it/s]




100%|█████████▉| 39432/39629 [2:42:03<00:54,  3.62it/s]




100%|█████████▉| 39433/39629 [2:42:04<00:53,  3.64it/s]




100%|█████████▉| 39434/39629 [2:42:04<00:53,  3.65it/s]




100%|█████████▉| 39435/39629 [2:42:04<00:53,  3.64it/s]




100%|█████████▉| 39436/39629 [2:42:05<00:52,  3.64it/s]




100%|█████████▉| 39437/39629 [2:42:05<00:52,  3.69it/s]




100%|█████████▉| 39438/39629 [2:42:

100%|█████████▉| 39531/39629 [2:42:31<00:26,  3.67it/s]




100%|█████████▉| 39532/39629 [2:42:32<00:26,  3.67it/s]




100%|█████████▉| 39533/39629 [2:42:32<00:26,  3.60it/s]




100%|█████████▉| 39534/39629 [2:42:32<00:26,  3.63it/s]




100%|█████████▉| 39535/39629 [2:42:32<00:25,  3.64it/s]




100%|█████████▉| 39536/39629 [2:42:33<00:25,  3.65it/s]




100%|█████████▉| 39537/39629 [2:42:33<00:25,  3.64it/s]




100%|█████████▉| 39538/39629 [2:42:33<00:25,  3.63it/s]




100%|█████████▉| 39539/39629 [2:42:33<00:24,  3.62it/s]




100%|█████████▉| 39540/39629 [2:42:34<00:24,  3.64it/s]




100%|█████████▉| 39541/39629 [2:42:34<00:24,  3.66it/s]




100%|█████████▉| 39542/39629 [2:42:34<00:23,  3.64it/s]




100%|█████████▉| 39543/39629 [2:42:35<00:23,  3.63it/s]




100%|█████████▉| 39544/39629 [2:42:35<00:23,  3.62it/s]




100%|█████████▉| 39545/39629 [2:42:35<00:23,  3.63it/s]




100%|█████████▉| 39546/39629 [2:42:35<00:24,  3.45it/s]




100%|█████████▉| 39547/39629 [2:42:36<00

In [17]:
df = pd.DataFrame({'name': ['Raphael', 'Donatello'],
                   'mask': ['red', 'purple'],
                   'weapon': ['sai', 'bo staff']})
df.to_csv('turtles.csv')